# Chuẩn bị data

In [ ]:
!git clone https://github.com/hoainhanpro/En_Vi_TextToSpeech.git
%cd En_Vi_TextToSpeech

In [ ]:
!pip install -q condacolab
import condacolab
condacolab.install()

In [ ]:
!conda install -c conda-forge montreal-forced-aligner=2.0.6


In [2]:
!mkdir -p raw_data/infore
!mkdir -p preprocessed_data/infore/TextGrid/infore
!mkdir -p output/ckpt/infore
!mkdir -p output/log/infore
!mkdir -p output/result/infore

In [3]:
# Di chuyển file wav và txt từ thư mục infore_16k_denoised vào raw_data/infore
!cp -r /kaggle/input/infore-16k-denoised/*.wav raw_data/infore/
!cp -r /kaggle/input/infore-16k-denoised/*.txt raw_data/infore/

# Đổi tên các file .txt thành .lab (theo yêu cầu của MFA)
!rename 's/\.txt$/.lab/' raw_data/infore/*.txt

# Align dữ liệu

In [ ]:
   !mfa train --clean -t ./temp ./raw_data/infore /kaggle/working/FastSpeech2_vi/lexicon/vi-new-lexicon.txt ./mfa/vi_new_mfa.zip
   !mfa align -t ./temp ./raw_data/infore ./mfa/vi-new-lexicon.dict ./mfa/vi_new_mfa.zip ./preprocessed_data/infore/TextGrid/infore1
   !python fix_align.py preprocessed_data/infore/TextGrid/infore1 preprocessed_data/infore/TextGrid/infore/

### Nén dữ liệu -> tải về lỡ có bị dừng session còn cứu được

In [ ]:
# Nén với mức độ nén tối đa
!cd /kaggle/working && zip -9 -r preprocessed_data_max.zip preprocessed_data

updating: preprocessed_data/ (stored 0%)
updating: preprocessed_data/infore/ (stored 0%)
updating: preprocessed_data/infore/val.txt (deflated 64%)
updating: preprocessed_data/infore/speakers.json (stored 0%)
updating: preprocessed_data/infore/duration/ (stored 0%)
updating: preprocessed_data/infore/stats.json (deflated 28%)
updating: preprocessed_data/infore/energy/ (stored 0%)
updating: preprocessed_data/infore/mel/ (stored 0%)
updating: preprocessed_data/infore/TextGrid/ (stored 0%)
updating: preprocessed_data/infore/TextGrid/infore08692.TextGrid (deflated 86%)
updating: preprocessed_data/infore/TextGrid/infore11321.TextGrid (deflated 87%)
updating: preprocessed_data/infore/TextGrid/infore11226.TextGrid (deflated 86%)
updating: preprocessed_data/infore/TextGrid/infore12828.TextGrid (deflated 87%)
updating: preprocessed_data/infore/TextGrid/infore14485.TextGrid (deflated 86%)
updating: preprocessed_data/infore/TextGrid/infore04559.TextGrid (deflated 87%)
updating: preprocessed_data/in

In [9]:
# Kiểm tra kích thước file
!ls -lh /kaggle/working/preprocessed_data_max.zip

-rw-r--r-- 1 root root 1.9G Mar 19 19:36 /kaggle/working/preprocessed_data_max.zip


# Tiền xử lý dữ liệu

In [80]:
# Sử dụng URL raw chính xác từ GitHub
!wget -O /kaggle/working/FastSpeech2_vi/preprocessor/preprocessor.py https://raw.githubusercontent.com/sp1007/FastSpeech2_vi/master/preprocessor/preprocessor.py

--2025-03-19 17:43:35--  https://raw.githubusercontent.com/sp1007/FastSpeech2_vi/master/preprocessor/preprocessor.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11020 (11K) [text/plain]
Saving to: ‘/kaggle/working/FastSpeech2_vi/preprocessor/preprocessor.py’

/kaggle/working/Fas 100%[===================>]  10.76K  --.-KB/s    in 0.001s  

2025-03-19 17:43:35 (12.9 MB/s) - ‘/kaggle/working/FastSpeech2_vi/preprocessor/preprocessor.py’ saved [11020/11020]



In [3]:
%%writefile /kaggle/working/FastSpeech2_vi/preprocessor/preprocessor.py
import os
import random
import json

import tgt
import librosa
import numpy as np
import pyworld as pw
from scipy.interpolate import interp1d
from sklearn.preprocessing import StandardScaler
from tqdm import tqdm

import audio as Audio


class Preprocessor:
    def __init__(self, config):
        self.config = config
        # Đường dẫn tuyệt đối cho raw_data
        self.in_dir = "/kaggle/working/raw_data"
        # Đường dẫn tuyệt đối cho preprocessed_data
        self.out_dir = "/kaggle/working/preprocessed_data/infore"
        self.val_size = config["preprocessing"]["val_size"]
        self.sampling_rate = config["preprocessing"]["audio"]["sampling_rate"]
        self.hop_length = config["preprocessing"]["stft"]["hop_length"]

        assert config["preprocessing"]["pitch"]["feature"] in [
            "phoneme_level",
            "frame_level",
        ]
        assert config["preprocessing"]["energy"]["feature"] in [
            "phoneme_level",
            "frame_level",
        ]
        self.pitch_phoneme_averaging = (
            config["preprocessing"]["pitch"]["feature"] == "phoneme_level"
        )
        self.energy_phoneme_averaging = (
            config["preprocessing"]["energy"]["feature"] == "phoneme_level"
        )

        self.pitch_normalization = config["preprocessing"]["pitch"]["normalization"]
        self.energy_normalization = config["preprocessing"]["energy"]["normalization"]

        self.STFT = Audio.stft.TacotronSTFT(
            config["preprocessing"]["stft"]["filter_length"],
            config["preprocessing"]["stft"]["hop_length"],
            config["preprocessing"]["stft"]["win_length"],
            config["preprocessing"]["mel"]["n_mel_channels"],
            config["preprocessing"]["audio"]["sampling_rate"],
            config["preprocessing"]["mel"]["mel_fmin"],
            config["preprocessing"]["mel"]["mel_fmax"],
        )

    def build_from_path(self):
        os.makedirs((os.path.join(self.out_dir, "mel")), exist_ok=True)
        os.makedirs((os.path.join(self.out_dir, "pitch")), exist_ok=True)
        os.makedirs((os.path.join(self.out_dir, "energy")), exist_ok=True)
        os.makedirs((os.path.join(self.out_dir, "duration")), exist_ok=True)

        print("🔍 Bắt đầu xử lý dữ liệu...")
        out = list()
        n_frames = 0
        pitch_scaler = StandardScaler()
        energy_scaler = StandardScaler()
        
        # Biến theo dõi dữ liệu và thống kê
        has_pitch_data = False
        has_energy_data = False
        total_files = 0
        successful_files = 0
        missing_textgrid = 0
        other_errors = 0

        # Compute pitch, energy, duration, and mel-spectrogram
        speakers = {"infore": 0}
        
        # Lấy danh sách file wav từ thư mục raw_data/infore
        wav_dir = os.path.join(self.in_dir, "infore")
        wav_files = [f for f in os.listdir(wav_dir) if f.endswith('.wav')]
        
        print(f"📊 Tổng số file wav: {len(wav_files)}")
        
        # Lấy danh sách file TextGrid
        textgrid_dir = os.path.join(self.out_dir, "TextGrid")
        textgrid_files = [f for f in os.listdir(textgrid_dir) if f.endswith('.TextGrid')]
        print(f"📊 Tổng số file TextGrid: {len(textgrid_files)}")
        
        # Kiểm tra thư mục phụ infore
        infore_dir = os.path.join(textgrid_dir, "infore")
        if os.path.exists(infore_dir):
            infore_files = [f for f in os.listdir(infore_dir) if f.endswith('.TextGrid')]
            print(f"📊 Số file TextGrid trong thư mục infore: {len(infore_files)}")
        
        # Hiển thị một số tên file TextGrid để kiểm tra định dạng
        if len(textgrid_files) > 0:
            print(f"🔍 Một số tên file TextGrid: {textgrid_files[:5]}")
        
        for wav_name in tqdm(wav_files):
            total_files += 1
            basename = wav_name.split(".")[0]
            
            # Kiểm tra các định dạng tên TextGrid khác nhau
            tg_formats = [
                # TextGrid có tiền tố "infore" + basename
                ("infore" + basename, os.path.join(self.out_dir, "TextGrid", "infore{}.TextGrid".format(basename))),
                # TextGrid trong thư mục infore
                (basename, os.path.join(self.out_dir, "TextGrid", "infore", "{}.TextGrid".format(basename))),
                # TextGrid có tên giống basename
                (basename, os.path.join(self.out_dir, "TextGrid", "{}.TextGrid".format(basename)))
            ]
            
            tg_found = False
            for tg_basename, tg_path in tg_formats:
                if os.path.exists(tg_path):
                    tg_found = True
                    print(f"✅ Tìm thấy TextGrid cho {basename}: {tg_path}")
                    ret = self.process_utterance("infore", basename, tg_basename, tg_path)
                    if ret is None:
                        other_errors += 1
                        print(f"❌ Xử lý thất bại: {basename}")
                        continue
                    else:
                        info, pitch, energy, n = ret
                        successful_files += 1
                        print(f"✅ Xử lý thành công: {basename}")
                    out.append(info)

                    if len(pitch) > 0:
                        pitch_scaler.partial_fit(pitch.reshape((-1, 1)))
                        has_pitch_data = True
                    if len(energy) > 0:
                        energy_scaler.partial_fit(energy.reshape((-1, 1)))
                        has_energy_data = True

                    n_frames += n
                    break
            
            if not tg_found:
                print(f"❌ Không tìm thấy TextGrid cho {basename}")
                missing_textgrid += 1

        print("\n📊 THỐNG KÊ XỬ LÝ:")
        print(f"Tổng số file wav: {total_files}")
        print(f"Số file xử lý thành công: {successful_files}")
        print(f"Số file thiếu TextGrid: {missing_textgrid}")
        print(f"Số file lỗi xử lý khác: {other_errors}")

        print("\n🔄 Tính toán thống kê...")
        # Perform normalization if necessary
        if self.pitch_normalization:
            if has_pitch_data:
                pitch_mean = pitch_scaler.mean_[0]
                pitch_std = pitch_scaler.scale_[0]
            else:
                print("⚠️ Không tìm thấy dữ liệu pitch. Sử dụng giá trị mặc định.")
                pitch_mean = 0
                pitch_std = 1
        else:
            # A numerical trick to avoid normalization...
            pitch_mean = 0
            pitch_std = 1
            
        if self.energy_normalization:
            if has_energy_data:
                energy_mean = energy_scaler.mean_[0]
                energy_std = energy_scaler.scale_[0]
            else:
                print("⚠️ Không tìm thấy dữ liệu energy. Sử dụng giá trị mặc định.")
                energy_mean = 0
                energy_std = 1
        else:
            energy_mean = 0
            energy_std = 1

        # Kiểm tra thư mục có file nào không trước khi chuẩn hóa
        pitch_dir = os.path.join(self.out_dir, "pitch")
        energy_dir = os.path.join(self.out_dir, "energy")
        
        pitch_files = os.listdir(pitch_dir) if os.path.exists(pitch_dir) else []
        energy_files = os.listdir(energy_dir) if os.path.exists(energy_dir) else []
        print(f"📊 Số file pitch: {len(pitch_files)}")
        print(f"📊 Số file energy: {len(energy_files)}")
        
        if len(pitch_files) > 0:
            pitch_min, pitch_max = self.normalize(pitch_dir, pitch_mean, pitch_std)
        else:
            print("⚠️ Không tìm thấy file pitch để chuẩn hóa.")
            pitch_min, pitch_max = 0.0, 1.0
            
        if len(energy_files) > 0:
            energy_min, energy_max = self.normalize(energy_dir, energy_mean, energy_std)
        else:
            print("⚠️ Không tìm thấy file energy để chuẩn hóa.")
            energy_min, energy_max = 0.0, 1.0

        # Save files
        with open(os.path.join(self.out_dir, "speakers.json"), "w") as f:
            f.write(json.dumps(speakers))

        with open(os.path.join(self.out_dir, "stats.json"), "w") as f:
            stats = {
                "pitch": [
                    float(pitch_min),
                    float(pitch_max),
                    float(pitch_mean),
                    float(pitch_std),
                ],
                "energy": [
                    float(energy_min),
                    float(energy_max),
                    float(energy_mean),
                    float(energy_std),
                ],
            }
            f.write(json.dumps(stats))

        print(
            "⏱️ Tổng thời lượng dữ liệu: {} giờ".format(
                n_frames * self.hop_length / self.sampling_rate / 3600
            )
        )

        random.shuffle(out)
        out = [r for r in out if r is not None]

        # Hiển thị số lượng dữ liệu trong tập train và val
        print(f"📊 Số mẫu trong tập train: {len(out) - self.val_size}")
        print(f"📊 Số mẫu trong tập validation: {min(self.val_size, len(out))}")

        # Write metadata
        with open(os.path.join(self.out_dir, "train.txt"), "w", encoding="utf-8") as f:
            for m in out[self.val_size :]:
                f.write(m + "\n")
        with open(os.path.join(self.out_dir, "val.txt"), "w", encoding="utf-8") as f:
            for m in out[: self.val_size]:
                f.write(m + "\n")

        return out

    def process_utterance(self, speaker, basename, tg_basename=None, tg_path=None):
        try:
            # Nếu không cung cấp tg_basename, mặc định là basename
            if tg_basename is None:
                tg_basename = basename
                
            # Chỉ định chính xác đường dẫn tới file wav và lab
            wav_path = os.path.join(self.in_dir, "infore", "{}.wav".format(basename))
            text_path = os.path.join(self.in_dir, "infore", "{}.lab".format(basename))
            
            # Sử dụng tg_path nếu được cung cấp, ngược lại tạo đường dẫn
            if tg_path is None:
                tg_path = os.path.join(self.out_dir, "TextGrid", "{}.TextGrid".format(tg_basename))

            # Kiểm tra tất cả các file có tồn tại không
            if not os.path.exists(wav_path):
                print(f"❌ Không tìm thấy file wav: {wav_path}")
                return None
                
            if not os.path.exists(text_path):
                print(f"❌ Không tìm thấy file lab: {text_path}")
                return None
                
            if not os.path.exists(tg_path):
                print(f"❌ Không tìm thấy file TextGrid: {tg_path}")
                return None

            # Get alignments
            textgrid = tgt.io.read_textgrid(tg_path)
            phone, duration, start, end = self.get_alignment(
                textgrid.get_tier_by_name("phones")
            )
                
            text = "{" + " ".join(phone) + "}"
            if start >= end:
                print(f"❌ Thời gian không hợp lệ: start={start}, end={end}")
                return None

            # Read and trim wav files
            wav, _ = librosa.load(wav_path)
            wav = wav[
                int(self.sampling_rate * start) : int(self.sampling_rate * end)
            ].astype(np.float32)

            # Read raw text
            with open(text_path, "r", encoding='utf-8') as f:
                raw_text = f.readline().strip("\n")

            # Compute fundamental frequency
            pitch, t = pw.dio(
                wav.astype(np.float64),
                self.sampling_rate,
                frame_period=self.hop_length / self.sampling_rate * 1000,
            )
            pitch = pw.stonemask(wav.astype(np.float64), pitch, t, self.sampling_rate)

            pitch = pitch[: sum(duration)]
            if np.sum(pitch != 0) <= 1:
                print(f"❌ Không đủ giá trị pitch cho {basename} (số giá trị khác 0: {np.sum(pitch != 0)})")
                return None

            # Compute mel-scale spectrogram and energy
            mel_spectrogram, energy = Audio.tools.get_mel_from_wav(wav, self.STFT)
            mel_spectrogram = mel_spectrogram[:, : sum(duration)]
            energy = energy[: sum(duration)]

            if self.pitch_phoneme_averaging:
                # Khởi tạo pitch_phoneme
                pitch_phoneme = np.zeros(len(duration))
                
                # perform linear interpolation
                nonzero_ids = np.where(pitch != 0)[0]
                if len(nonzero_ids) > 0:  # Thêm kiểm tra để tránh lỗi
                    interp_fn = interp1d(
                        nonzero_ids,
                        pitch[nonzero_ids],
                        fill_value=(pitch[nonzero_ids[0]], pitch[nonzero_ids[-1]]),
                        bounds_error=False,
                    )
                    pitch = interp_fn(np.arange(0, len(pitch)))

                    # Phoneme-level average
                    pos = 0
                    for i, d in enumerate(duration):
                        if d > 0:
                            pitch_phoneme[i] = np.mean(pitch[pos : pos + d])
                        else:
                            pitch_phoneme[i] = 0
                        pos += d
                    pitch = pitch_phoneme

            if self.energy_phoneme_averaging:
                # Khởi tạo energy_phoneme
                energy_phoneme = np.zeros(len(duration))
                
                # Phoneme-level average
                pos = 0
                for i, d in enumerate(duration):
                    if d > 0:
                        energy_phoneme[i] = np.mean(energy[pos : pos + d])
                    else:
                        energy_phoneme[i] = 0
                    pos += d
                energy = energy_phoneme

            # Save files
            dur_filename = "{}-duration-{}.npy".format(speaker, basename)
            np.save(os.path.join(self.out_dir, "duration", dur_filename), duration)

            pitch_filename = "{}-pitch-{}.npy".format(speaker, basename)
            np.save(os.path.join(self.out_dir, "pitch", pitch_filename), pitch)

            energy_filename = "{}-energy-{}.npy".format(speaker, basename)
            np.save(os.path.join(self.out_dir, "energy", energy_filename), energy)

            mel_filename = "{}-mel-{}.npy".format(speaker, basename)
            np.save(
                os.path.join(self.out_dir, "mel", mel_filename),
                mel_spectrogram.T,
            )

            return (
                "|".join([basename, speaker, text, raw_text]),
                self.remove_outlier(pitch),
                self.remove_outlier(energy),
                mel_spectrogram.shape[1],
            )
        except Exception as e:
            print(f"❌ Lỗi khi xử lý {basename}: {str(e)}")
            import traceback
            traceback.print_exc()
            return None

    def get_alignment(self, tier):
        sil_phones = ["sil", "sp", "spn"]

        phones = []
        durations = []
        start_time = 0
        end_time = 0
        end_idx = 0
        for t in tier._objects:
            s, e, p = t.start_time, t.end_time, t.text

            # Trim leading silences
            if phones == []:
                if p in sil_phones:
                    continue
                else:
                    start_time = s

            if p not in sil_phones:
                # For ordinary phones
                phones.append(p)
                end_time = e
                end_idx = len(phones)
            else:
                # For silent phones
                phones.append(p)

            durations.append(
                int(
                    np.round(e * self.sampling_rate / self.hop_length)
                    - np.round(s * self.sampling_rate / self.hop_length)
                )
            )

        # Trim tailing silences
        phones = phones[:end_idx]
        durations = durations[:end_idx]

        return phones, durations, start_time, end_time

    def remove_outlier(self, values):
        values = np.array(values)
        p25 = np.percentile(values, 25)
        p75 = np.percentile(values, 75)
        lower = p25 - 1.5 * (p75 - p25)
        upper = p75 + 1.5 * (p75 - p25)
        normal_indices = np.logical_and(values > lower, values < upper)

        return values[normal_indices]

    def normalize(self, in_dir, mean, std):
        max_value = np.finfo(np.float64).min
        min_value = np.finfo(np.float64).max
        for filename in os.listdir(in_dir):
            filename = os.path.join(in_dir, filename)
            values = (np.load(filename) - mean) / std
            np.save(filename, values)

            max_value = max(max_value, max(values))
            min_value = min(min_value, min(values))

        return min_value, max_value

Overwriting /kaggle/working/FastSpeech2_vi/preprocessor/preprocessor.py


In [18]:
!nvidia-smi

Wed Mar 19 18:30:26 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   38C    P8              9W /   70W |       1MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [ ]:
!pip install torch torchvision torchaudio --extra-index-url https://download.pytorch.org/whl/cu124

In [1]:
import torch
print(torch.__version__)           # Phiên bản PyTorch
print(torch.cuda.is_available())   # Phải trả về True
print(torch.version.cuda)          # Phiên bản CUDA của PyTorch
print(torch.cuda.device_count())   # Số lượng GPU (nên là 2)
print(torch.cuda.get_device_name(0))  # Tên GPU (Tesla T4)

2.6.0+cu124
True
12.4
2
Tesla T4


In [ ]:
!python /kaggle/working/FastSpeech2_vi/preprocess.py /kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml

# Train model

In [3]:
with open('/kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml', 'r') as file:
    content = file.read()
    
# Thay đổi đường dẫn corpus_path để phù hợp với Kaggle
content = content.replace('./input/infore', './raw_data/infore')
    
with open('/kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml', 'w') as file:
    file.write(content)

In [5]:
# Thêm code để lưu checkpoint vào thư mục output của Kaggle
with open('/kaggle/working/FastSpeech2_vi/train.py', 'r') as file:
    content = file.read()
    
# Thêm code để lưu checkpoint định kỳ vào thư mục output của Kaggle
content = content.replace(
    'if step % save_step == 0:',
    'if step % save_step == 0:\n                    # Lưu checkpoint vào thư mục output của Kaggle\n                    kaggle_output_path = "/kaggle/working/checkpoints"\n                    os.makedirs(kaggle_output_path, exist_ok=True)\n                    torch.save(\n                        {\n                            "model": model.module.state_dict(),\n                            "optimizer": optimizer._optimizer.state_dict(),\n                        },\n                        os.path.join(\n                            kaggle_output_path,\n                            "{}.pth.tar".format(step),\n                        ),\n                    )'
)
    
with open('/kaggle/working/FastSpeech2_vi/train.py', 'w') as file:
    file.write(content)

In [ ]:
!pip install tensorboard

In [ ]:
!pip install unidecode

In [12]:
!pip install inflect

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.0/63.0 kB 4.3 MB/s eta 0:00:00


In [5]:
ls -la /kaggle/working/preprocessed_data/infore/mel | wc -l

14762


In [10]:
%%writefile /kaggle/working/FastSpeech2_vi/utils/model.py
import os
import json

import torch
import numpy as np
import hifigan  # Đảm bảo có dòng import này

from .tools import to_device, log, synth_one_sample
from model import FastSpeech2, ScheduledOptim


def get_model(args, configs, device, train=False):
    (preprocess_config, model_config, train_config) = configs

    model = FastSpeech2(preprocess_config, model_config).to(device)
    if args.restore_step:
        ckpt_path = os.path.join(
            train_config["path"]["ckpt_path"],
            "{}.pth.tar".format(args.restore_step),
        )
        ckpt = torch.load(ckpt_path)
        model.load_state_dict(ckpt["model"])

    if train:
        scheduled_optim = ScheduledOptim(
            model, train_config, model_config, args.restore_step
        )
        if args.restore_step:
            scheduled_optim.load_state_dict(ckpt["optimizer"])
        model.train()
        return model, scheduled_optim

    model.eval()
    model.requires_grad_ = False
    return model


def get_param_num(model):
    num_param = sum(param.numel() for param in model.parameters())
    return num_param


def get_vocoder(config, device):
    name = config["vocoder"]["model"]
    speaker = config["vocoder"]["speaker"]

    if name == "MelGAN":
        if speaker == "LJSpeech":
            vocoder = torch.hub.load(
                "descriptinc/melgan-neurips", "load_melgan", "linda_johnson"
            )
        elif speaker == "universal":
            vocoder = torch.hub.load(
                "descriptinc/melgan-neurips", "load_melgan", "multi_speaker"
            )
        vocoder.mel2wav.eval()
        vocoder.mel2wav.to(device)
    elif name == "HiFi-GAN":
        # Sửa đường dẫn để sử dụng đường dẫn tuyệt đối
        config_path = os.path.join("/kaggle/working/FastSpeech2_vi", "hifigan", "config.json")
        with open(config_path, "r") as f:
            config = json.load(f)
        config = hifigan.AttrDict(config)
        vocoder = hifigan.Generator(config)
        if speaker == "LJSpeech":
            ckpt_path = os.path.join("/kaggle/working/FastSpeech2_vi", "hifigan", "generator_LJSpeech.pth.tar")
        elif speaker == "universal":
            ckpt_path = os.path.join("/kaggle/working/FastSpeech2_vi", "hifigan", "generator_universal.pth.tar")
        ckpt = torch.load(ckpt_path)
        vocoder.load_state_dict(ckpt["generator"])
        vocoder.eval()
        vocoder.remove_weight_norm()
        vocoder.to(device)

    return vocoder


def vocoder_infer(mels, vocoder, model_config, preprocess_config, lengths=None):
    name = model_config["vocoder"]["model"]
    with torch.no_grad():
        if name == "MelGAN":
            wavs = vocoder.inverse(mels / np.log(10))
        elif name == "HiFi-GAN":
            wavs = vocoder(mels).squeeze(1)

    wav_reconstruction = []
    for i in range(len(mels)):
        if lengths is not None:
            wav_reconstruction.append(
                wavs[i, : lengths[i] * preprocess_config["preprocessing"]["stft"]["hop_length"]]
                .cpu()
                .numpy()
            )
        else:
            wav_reconstruction.append(wavs[i].cpu().numpy())

    return wav_reconstruction

Overwriting /kaggle/working/FastSpeech2_vi/utils/model.py


In [12]:
%%writefile /kaggle/working/FastSpeech2_vi/dataset.py
import json
import math
import os

import numpy as np
from torch.utils.data import Dataset

from text import text_to_sequence
from utils.tools import pad_1D, pad_2D


class Dataset(Dataset):
    def __init__(
        self, filename, preprocess_config, train_config, sort=False, drop_last=False
    ):
        self.dataset_name = preprocess_config["dataset"]
        self.preprocessed_path = preprocess_config["path"]["preprocessed_path"]
        self.cleaners = preprocess_config["preprocessing"]["text"]["text_cleaners"]
        self.batch_size = train_config["optimizer"]["batch_size"]

        self.basename, self.speaker, self.text, self.raw_text = self.process_meta(
            filename
        )
        with open(os.path.join(self.preprocessed_path, "speakers.json")) as f:
            self.speaker_map = json.load(f)
        self.sort = sort
        self.drop_last = drop_last

    def __len__(self):
        return len(self.text)

    def __getitem__(self, idx):
        basename = self.basename[idx]
        speaker = self.speaker[idx]
        speaker_id = self.speaker_map[speaker]
        raw_text = self.raw_text[idx]
        phone = np.array(text_to_sequence(self.text[idx], self.cleaners))
        
        # Đường dẫn tới các file đặc trưng
        mel_path = os.path.join(
            self.preprocessed_path,
            "mel",
            "{}-mel-{}.npy".format(speaker, basename),
        )
        pitch_path = os.path.join(
            self.preprocessed_path,
            "pitch",
            "{}-pitch-{}.npy".format(speaker, basename),
        )
        energy_path = os.path.join(
            self.preprocessed_path,
            "energy",
            "{}-energy-{}.npy".format(speaker, basename),
        )
        duration_path = os.path.join(
            self.preprocessed_path,
            "duration",
            "{}-duration-{}.npy".format(speaker, basename),
        )

        # Đọc và chuyển đổi dữ liệu sang float32
        mel = np.load(mel_path).astype(np.float32)
        pitch = np.load(pitch_path).astype(np.float32)
        energy = np.load(energy_path).astype(np.float32)
        duration = np.load(duration_path).astype(np.float32)

        sample = {
            "id": basename,
            "speaker": speaker_id,
            "text": phone,
            "raw_text": raw_text,
            "mel": mel,
            "pitch": pitch,
            "energy": energy,
            "duration": duration,
        }

        return sample

    def process_meta(self, filename):
        with open(
            os.path.join(self.preprocessed_path, filename), "r", encoding="utf-8"
        ) as f:
            name = []
            speaker = []
            text = []
            raw_text = []
            for line in f.readlines():
                n, s, t, r = line.strip("\n").split("|")
                name.append(n)
                speaker.append(s)
                text.append(t)
                raw_text.append(r)
            return name, speaker, text, raw_text

    def reprocess(self, data, idxs):
        ids = [data[idx]["id"] for idx in idxs]
        speakers = [data[idx]["speaker"] for idx in idxs]
        texts = [data[idx]["text"] for idx in idxs]
        raw_texts = [data[idx]["raw_text"] for idx in idxs]
        mels = [data[idx]["mel"] for idx in idxs]
        pitches = [data[idx]["pitch"] for idx in idxs]
        energies = [data[idx]["energy"] for idx in idxs]
        durations = [data[idx]["duration"] for idx in idxs]

        text_lens = np.array([text.shape[0] for text in texts])
        mel_lens = np.array([mel.shape[0] for mel in mels])

        speakers = np.array(speakers)
        texts = pad_1D(texts)
        mels = pad_2D(mels)
        pitches = pad_1D(pitches)
        energies = pad_1D(energies)
        durations = pad_1D(durations)

        return (
            ids,
            raw_texts,
            speakers,
            texts,
            text_lens,
            max(text_lens),
            mels,
            mel_lens,
            max(mel_lens),
            pitches,
            energies,
            durations,
        )

    def collate_fn(self, data):
        data_size = len(data)

        if self.sort:
            len_arr = np.array([d["text"].shape[0] for d in data])
            idx_arr = np.argsort(-len_arr)
        else:
            idx_arr = np.arange(data_size)

        tail = idx_arr[len(idx_arr) - (len(idx_arr) % self.batch_size) :]
        idx_arr = idx_arr[: len(idx_arr) - (len(idx_arr) % self.batch_size)]
        idx_arr = idx_arr.reshape((-1, self.batch_size)).tolist()
        if not self.drop_last and len(tail) > 0:
            idx_arr += [tail.tolist()]

        output = list()
        for idx in idx_arr:
            output.append(self.reprocess(data, idx))

        return output


class TextDataset(Dataset):
    def __init__(self, filepath, preprocess_config):
        self.cleaners = preprocess_config["preprocessing"]["text"]["text_cleaners"]

        self.basename, self.speaker, self.text, self.raw_text = self.process_meta(
            filepath
        )
        with open(
            os.path.join(
                preprocess_config["path"]["preprocessed_path"], "speakers.json"
            )
        ) as f:
            self.speaker_map = json.load(f)

    def __len__(self):
        return len(self.text)

    def __getitem__(self, idx):
        basename = self.basename[idx]
        speaker = self.speaker[idx]
        speaker_id = self.speaker_map[speaker]
        raw_text = self.raw_text[idx]
        phone = np.array(text_to_sequence(self.text[idx], self.cleaners))

        return (basename, speaker_id, phone, raw_text)

    def process_meta(self, filename):
        with open(filename, "r", encoding="utf-8") as f:
            name = []
            speaker = []
            text = []
            raw_text = []
            for line in f.readlines():
                n, s, t, r = line.strip("\n").split("|")
                name.append(n)
                speaker.append(s)
                text.append(t)
                raw_text.append(r)
            return name, speaker, text, raw_text

    def collate_fn(self, data):
        ids = [d[0] for d in data]
        speakers = np.array([d[1] for d in data])
        texts = [d[2] for d in data]
        raw_texts = [d[3] for d in data]
        text_lens = np.array([text.shape[0] for text in texts])

        texts = pad_1D(texts)

        return ids, raw_texts, speakers, texts, text_lens, max(text_lens)

Overwriting /kaggle/working/FastSpeech2_vi/dataset.py


In [18]:
%%writefile /kaggle/working/FastSpeech2_vi/config/infore/train.yaml
optimizer:
  batch_size: 16
  group_size: 1
  betas: [0.9, 0.98]  # Thêm dòng này
  eps: 0.000000001  # Thêm cả eps nếu cần
  weight_decay: 0.0  # Thêm cả weight_decay nếu cần
  grad_clip_thresh: 1.0  # Thêm cả giới hạn gradient clipping
  grad_acc_step: 1  # Thêm số bước tích lũy gradient
  warm_up_step: 4000  # Thêm số bước khởi động
  anneal_steps: [300000, 400000, 500000]  # Thêm các bước giảm learning rate
  anneal_rate: 0.3  # Thêm tỉ lệ giảm learning rate

path:
  ckpt_path: "./output/ckpt/infore"
  log_path: "./output/log/infore"
  result_path: "./output/result/infore"
  
step:
  total_step: 10000  # Đã giảm từ 900,000 xuống 10,000
  log_step: 100
  synth_step: 1000
  val_step: 1000
  save_step: 1000

seed: 1234  # Thêm seed để kết quả tái tạo được

Overwriting /kaggle/working/FastSpeech2_vi/config/infore/train.yaml


In [20]:
%%writefile /kaggle/working/FastSpeech2_vi/config/infore/train.yaml
path:
  ckpt_path: "/kaggle/working/output/ckpt/infore"
  log_path: "/kaggle/working/output/log/infore"
  result_path: "/kaggle/working/output/result/infore"
optimizer:
  batch_size: 16
  betas: [0.9, 0.98]
  eps: 0.000000001
  weight_decay: 0.0
  grad_clip_thresh: 1.0
  grad_acc_step: 1
  warm_up_step: 4000
  anneal_steps: [300000, 400000, 500000]
  anneal_rate: 0.3
step:
  total_step: 10000  # Giảm xuống để huấn luyện nhanh hơn
  log_step: 100
  synth_step: 1000
  val_step: 1000
  save_step: 1000

Overwriting /kaggle/working/FastSpeech2_vi/config/infore/train.yaml


In [21]:
%%writefile /kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml
dataset: "infore"

path:
  corpus_path: "/kaggle/working/raw_data/infore"
  lexicon_path: "/kaggle/working/FastSpeech2_vi/lexicon/vi-new-lexicon.txt"
  raw_path: "/kaggle/working/raw_data/"
  preprocessed_path: "/kaggle/working/preprocessed_data/infore"

preprocessing:
  val_size: 512
  text:
    text_cleaners: ["vietnamese_cleaners"]
    language: "vi"
  audio:
    sampling_rate: 22050
    max_wav_value: 32768.0
  stft:
    filter_length: 1024
    hop_length: 256
    win_length: 1024
  mel:
    n_mel_channels: 80
    mel_fmin: 0
    mel_fmax: 8000 # please set to 8000 for HiFi-GAN vocoder, set to null for MelGAN vocoder
  pitch:
    feature: "phoneme_level" # support 'phoneme_level' or 'frame_level'
    normalization: True
  energy:
    feature: "phoneme_level" # support 'phoneme_level' or 'frame_level'
    normalization: True

Overwriting /kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml


In [ ]:
!python /kaggle/working/FastSpeech2_vi/train.py -p /kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml -m /kaggle/working/FastSpeech2_vi/config/infore/model.yaml -t /kaggle/working/FastSpeech2_vi/config/infore/train.yaml

Prepare training ...
Number of FastSpeech2 Parameters: 35272513
/usr/local/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
Removing weight norm...
Training:   1%|▎                             | 97/10000 [00:31<47:45,  3.46it/s]
                                                                                
Step 100/10000, Total Loss: 12.3027, Mel Loss: 4.8796, Mel PostNet Loss: 4.5611, Pitch Loss: 1.3542, Energy Loss: 1.0359, Duration Loss: 0.4720
Training:   1%|▎                          | 118/10000 [00:38<1:01:14,  2.69it/s]

# Lưu checkpoint đề phòng timeout

In [ ]:
# Lưu checkpoint vào Google Drive
from google.colab import drive
drive.mount('/content/drive')

# Sao chép checkpoint từ thư mục làm việc của Kaggle vào Google Drive
!cp -r /kaggle/working/checkpoints/* /content/drive/MyDrive/fastspeech2_checkpoints/

In [ ]:
# # Tạo notebook mới và tải lại checkpoint
# !mkdir -p output/ckpt/infore
# !cp /content/drive/MyDrive/fastspeech2_checkpoints/100000.pth.tar output/ckpt/infore/

# # Tiếp tục huấn luyện
# !python train.py --restore_step 100000 -p config/infore/preprocess.yaml -m config/infore/model.yaml -t config/infore/train.yaml

Thử nghiệm model

In [ ]:
!python synthesize.py --text "Xin chào, tôi là trợ lý ảo tiếng Việt được huấn luyện bởi Hoài Nhân" --restore_step 100000 --mode single -p /kaggle/working/FastSpeech2_vi/config/infore/preprocess.yaml -m /kaggle/working/FastSpeech2_vi/config/infore/model.yaml -t /kaggle/working/FastSpeech2_vi/config/infore/train.yaml